In [1]:
# necessary imports
import sys
import os
import json
import requests
import numpy as np
import pandas as pd
import plotly.express as px

from sklearn.preprocessing import PolynomialFeatures
from json import loads, dumps, dump

sys.path.append(os.path.abspath(os.path.join('..')))

from app.fetcher import fetch_maps, fetch_scores, fetch_profile
from app.models import predict_scores

### Fetch Maps and Scores

In [2]:
# fetch ranked maps (takes 1-2 min)
# maps_df = fetch_maps()
# maps_df.to_csv("ranked_maps.csv")

In [3]:
# load ranked maps
maps_df = pd.read_csv("ranked_maps.csv")

In [4]:
maps_df.head()

Unnamed: 0 leaderboardId songId  \
0           0         57c31    57c   
1           1         57c51    57c   
2           2         57c71    57c   
3           3      1fd41x11  1fd41   
4           4      1fd41x31  1fd41   

                                               cover  \
0  https://eu.cdn.beatsaver.com/f15082586d31d238c...   
1  https://eu.cdn.beatsaver.com/f15082586d31d238c...   
2  https://eu.cdn.beatsaver.com/f15082586d31d238c...   
3  https://eu.cdn.beatsaver.com/1fb8d26ef00049d75...   
4  https://eu.cdn.beatsaver.com/1fb8d26ef00049d75...   

                                           fullCover       name  \
0  https://cdn.assets.beatleader.xyz/songcover-57...        Zzz   
1  https://cdn.assets.beatleader.xyz/songcover-57...        Zzz   
2  https://cdn.assets.beatleader.xyz/songcover-57...        Zzz   
3  https://cdn.assets.beatleader.xyz/songcover-1f...  Zombified   
4  https://cdn.assets.beatleader.xyz/songcover-1f...  Zombified   

            subName              author    mapper    bpm  ...  passRating  \
0  by Sasaki Sayaka            Todokete  todokete  154.0  ...    0.992113   
1  by Sasaki Sayaka            Todokete  todokete  154.0  ...    2.433202   
2  by Sasaki Sayaka            Todokete  todokete  154.0  ...    3.184074   
3               NaN  Falling In Reverse   Bytrius  182.0  ...    1.331649   
4               NaN  Falling In Reverse   Bytrius  182.0  ...    2.345820   

   accRating  techRating                                    modifiersRating  \
0   5.772469    3.247698  {'id': 8496, 'ssPredictedAcc': 0.988283, 'ssPa...   
1   7.259916    6.221073  {'id': 8497, 'ssPredictedAcc': 0.9849364, 'ssP...   
2   8.040394    8.696276  {'id': 8498, 'ssPredictedAcc': 0.98291683, 'ss...   
3   5.175914    1.158910  {'id': 7615, 'ssPredictedAcc': 0.9898724, 'ssP...   
4   6.326489    1.984545  {'id': 7616, 'ssPredictedAcc': 0.9872046, 'ssP...   

   difficultyName      type  starsMod passRatingMod  accRatingMod  \
0          Normal  Accuracy  3.565262      0.992113      5.772469   
1            Hard      Tech  5.456755      2.433202      7.259916   
2          Expert      Tech  6.634682      3.184074      8.040394   
3            Easy  Accuracy  2.996581      1.331649      5.175914   
4          Normal  Accuracy  4.168840      2.345820      6.326489   

   techRatingMod  
0       3.247698  
1       6.221073  
2       8.696276  
3       1.158910  
4       1.984545  

[5 rows x 22 columns]

In [5]:
# fetch player scores (takes 6-20 sec.)
id = "thinkingswag"
scores_df = fetch_scores(id)

In [6]:
scores_df.head()

leaderboardId songId                                              cover  \
0        2b85fxx71  2b85f  https://eu.cdn.beatsaver.com/09fd6d30c55f6d721...   
1  3bcf5xxxxxxxx91  3bcf5  https://cdn.beatsaver.com/187bea15de6bd7301239...   
2          1cd7791  1cd77  https://eu.cdn.beatsaver.com/08d67c25e377d2013...   
3          2a1b391  2a1b3  https://eu.cdn.beatsaver.com/604ac21a79c26207c...   
4          1cdc691  1cdc6  https://eu.cdn.beatsaver.com/eaddeb51358bbd688...   

                                           fullCover  \
0  https://cdn.assets.beatleader.xyz/songcover-2b...   
1  https://cdn.assets.beatleader.xyz/songcover-3b...   
2  https://cdn.assets.beatleader.xyz/songcover-1c...   
3  https://cdn.assets.beatleader.xyz/songcover-2a...   
4  https://cdn.assets.beatleader.xyz/songcover-1c...   

                                                name            subName  \
0  At Least Speedcore Artists Aren't In It For Th...                      
1                                        nieuwe tune                      
2                                          Deception                      
3                      II. Anal Prolapse Suffocation                      
4                   We Like To Party! (The Vengabus)  [Fvrwvrd Bootleg]   

                           author         mapper    bpm  duration  ...  \
0             Loffciamcore & Imil          Slayx  260.0       143  ...   
1  gladde paling & vieze vaatdoek  Stupidity-101  180.0        93  ...   
2               Dance Gavin Dance         cerret  316.0       233  ...   
3              Infant Annihilator        Vilawes  350.0       182  ...   
4                       Vengaboys         cerret  320.0       125  ...   

   accuracy         pp  rank  modifiers fullCombo currentMods predictedMods  \
0  0.974111  840.22034     2         SF      True        [SF]          [SF]   
1  0.941264  794.43090     2         FS     False        [FS]          [FS]   
2  0.969104  783.93976     3         SF     False        [SF]          [SF]   
3  0.974313  773.77510     3         FS      True        [FS]          [FS]   
4  0.972415  768.43270     3         FS      True        [FS]          [FS]   

     timePost             dateSet      timeAgo  
0  1674691102 2023-01-25 18:58:22  2 years ago  
1  1734137356 2024-12-13 19:49:16   1 year ago  
2  1684004676 2023-05-13 15:04:36  2 years ago  
3  1678923525 2023-03-15 19:38:45  2 years ago  
4  1678922855 2023-03-15 19:27:35  2 years ago  

[5 rows x 31 columns]

In [7]:
# calculate days since scores were set
max_date = scores_df["dateSet"].max()
scores_df["days_since"] = (max_date - scores_df["dateSet"]).dt.days

### Train Model

Decay Function: $\text{Weight}(t) = e^{-\lambda \times \frac{\text{days since}}{14}}$

In [8]:
# apply weighted decay function so newer scores have more influence on the model
lambda_value = 0.1
decay_weights = np.exp(-lambda_value * scores_df["days_since"] / 14) # 2 weeks
scores_df["decay_weights"] = decay_weights

In [9]:
# set up features for exponential regression model

# modified ratings as independent variables
X = scores_df[["passRatingMod", "accRatingMod", "techRatingMod"]].values.reshape(-1, 3)
X_poly = PolynomialFeatures(degree=2, include_bias=False).fit_transform(X)

# dependent variable; invert to mimic downward curve
y = scores_df["accuracy"].to_numpy().reshape(-1, 1)
y_inv = (1 - scores_df["accuracy"]).to_numpy().reshape(-1, 1)
y_inv_log = np.log(y_inv)

LOBF Equation: $\text{model} = (X^TWX)^{-1}X^TWy$

In [10]:
# train model
W = np.diag(decay_weights)
X_poly_bias = np.column_stack([np.ones(X_poly.shape[0]), X_poly])

XtW = np.matmul(X_poly_bias.T, W)
XtWX_inv = np.linalg.inv(np.matmul(XtW, X_poly_bias))
XtWy = np.matmul(XtW, y_inv_log)

model = np.matmul(XtWX_inv, XtWy)
model

array([[-4.70547070e+00],
       [-5.56906954e-02],
       [ 8.24295613e-02],
       [ 3.17695114e-02],
       [ 5.05540603e-03],
       [-1.55732355e-03],
       [-4.59225908e-03],
       [ 4.71181072e-03],
       [-5.56774999e-03],
       [ 8.96782753e-03]])

### Predict Scores

In [11]:
# predict scores
ypreds_inv = np.dot(X_poly, model[1:]) + model[0]
ypreds = 1 - np.exp(ypreds_inv)

scores_df["pred_accuracy"] = ypreds
scores_df[["accuracy", "pred_accuracy"]].head()

accuracy  pred_accuracy
0  0.974111       0.959431
1  0.941264       0.940980
2  0.969104       0.959099
3  0.974313       0.965180
4  0.972415       0.964236

### Visualizations

In [12]:
px.scatter(scores_df, x="stars", y="accuracy", color="decay_weights", color_continuous_scale="magenta",
           hover_data=["name", "mapper", "type", "difficultyName", "days_since", 
                       "passRatingMod", "accRatingMod", "techRatingMod"], 
           title="Decay Weights for Scores")

In [13]:
scores_df['accuracy_type'] = 'Actual'

comb_df = scores_df[['stars', 'pred_accuracy']].copy()
comb_df['accuracy_type'] = 'Predicted'
comb_df = comb_df.rename(columns={'pred_accuracy': 'accuracy'})

combined_df = pd.concat([scores_df[['stars', 'accuracy', 'accuracy_type']], comb_df[['stars', 'accuracy', 'accuracy_type']]], ignore_index=True)

px.scatter(combined_df, x="stars", y="accuracy", color="accuracy_type", title="Actual vs. Predicted Accuracy")

### All Predictions

In [14]:
# predict for all maps
predictions_df = predict_scores(model, scores_df, maps_df)
predictions_df.head()

leaderboardId songId  \
808   3ce7axxxxxxxxxxx91  3ce7a   
430             24d9bx91  24d9b   
1815      31d13xxxxxxx91  31d13   
2523           338afxx91  338af   
3315          40127xxx91  40127   

                                                  cover  \
808   https://cdn.beatsaver.com/6343bbda0b1c75d52423...   
430   https://eu.cdn.beatsaver.com/6e9498f81bbf26fa4...   
1815  https://cdn.beatsaver.com/881bdd4f5e7c05021f7c...   
2523  https://na.cdn.beatsaver.com/c678f67c54e8258ac...   
3315  https://cdn.beatsaver.com/6316743b3a2900a75ff5...   

                                              fullCover  \
808   https://cdn.assets.beatleader.xyz/songcover-3c...   
430   https://cdn.assets.beatleader.xyz/songcover-24...   
1815  https://cdn.assets.beatleader.xyz/songcover-31...   
2523  https://cdn.assets.beatleader.xyz/songcover-33...   
3315  https://cdn.assets.beatleader.com/songcover-40...   

                           name           subName           author  \
808        The Purple Dimension  Extended Version       ToonTubers   
430                   Yggdrasil               NaN  Gram VS Kobaryo   
1815                  Luminency               NaN          Ludicin   
2523                      Feral               NaN         meganeko   
3315  Apocalypse Simulator v2.0               NaN          Kobaryo   

                       mapper    bpm  duration  ... predictedMods  \
808       Cratornugget & ViSi  464.0       187  ...           NaN   
430              GalaxyMaster  200.0       423  ...           NaN   
1815                     Fnyt  350.0       265  ...           NaN   
2523  miitchel, Jabob & Hades  160.0       269  ...           NaN   
3315                     ViSi  222.0       235  ...           NaN   

     currentAccuracy  predictedAccuracy  accuracyGained  currentPP  \
808              0.0           0.955786        0.955786        0.0   
430              0.0           0.964346        0.964346        0.0   
1815             0.0           0.963472        0.963472        0.0   
2523             0.0           0.960764        0.960764        0.0   
3315             0.0           0.962292        0.962292        0.0   

      predictedPP       maxPP  unweightedPPGain  weightedPPGain  weight  
808    783.912676  783.912676        783.912676      704.737496   0.899  
430    750.574050  750.574050        750.574050      525.401835   0.700  
1815   749.092097  749.092097        749.092097      471.178929   0.629  
2523   746.647139  746.647139        746.647139      437.535224   0.586  
3315   746.456933  746.456933        746.456933      437.423763   0.586  

[5 rows x 36 columns]

In [15]:
predictions_df[predictions_df["status"] == "unplayed"].modifiersRating.head()

808     {'id': 1246990, 'ssPredictedAcc': 0.96775866, ...
430     {'id': 299783, 'ssPredictedAcc': 0.97095835, '...
1815    {'id': 595920, 'ssPredictedAcc': 0.9686222, 's...
2523    {'id': 1132162, 'ssPredictedAcc': 0.9665326, '...
3315    {'id': 1299933, 'ssPredictedAcc': 0.9738307, '...
Name: modifiersRating, dtype: object

In [16]:
# api reponse
resp = predictions_df.to_json(orient="records")
parsed = loads(resp)
print(dumps(parsed, indent=4))

[
    {
        "leaderboardId": "3ce7axxxxxxxxxxx91",
        "songId": "3ce7a",
        "cover": "https://cdn.beatsaver.com/6343bbda0b1c75d52423e6273858c1d80b6f9326.jpg",
        "fullCover": "https://cdn.assets.beatleader.xyz/songcover-3ce7axxxxxxxxxxx-full.webp",
        "name": "The Purple Dimension",
        "subName": "Extended Version",
        "author": "ToonTubers",
        "mapper": "Cratornugget & ViSi",
        "bpm": 464.0,
        "duration": 187,
        "difficultyName": "ExpertPlus",
        "type": "Speed",
        "stars": 15.605963,
        "passRating": 16.897497,
        "accRating": 12.630503,
        "techRating": 6.4419417,
        "starsMod": 15.605963,
        "passRatingMod": 16.897497,
        "accRatingMod": 12.630503,
        "techRatingMod": 6.4419417,
        "modifiersRating": "{'id': 1246990, 'ssPredictedAcc': 0.96775866, 'ssPassRating': 14.323344, 'ssAccRating': 11.949681, 'ssTechRating': 6.4117107, 'ssStars': 13.714355, 'fsPredictedAcc': 0.9584569,

In [17]:
# save predictions to json file
predictions_df.to_json("predictions.json", orient="records", compression="infer")

In [18]:
# fetch player profile
fetch_profile("thinkingswag")

{'id': '76561199104169308',
 'name': 'thinking',
 'alias': 'thinkingswag',
 'avatar': 'https://cdn.assets.beatleader.xyz/76561199104169308R23.png',
 'country': 'US',
 'pp': 21318.164,
 'rank': 6,
 'countryRank': 4}

In [19]:
# save api response
url = f"http://127.0.0.1:8000/recommendations/{id}"
resp = requests.get(url)
resp.raise_for_status()
data = resp.json()
with open("response.json", "w") as json_file:
  dump(data, json_file, indent=4)